In [2]:
from numpy.random import seed
seed(4)

In [3]:
import os
import math
import nltk
import numpy as np
import pandas as pd
import tensorflow as tf

from sklearn.preprocessing import StandardScaler
from tensorflow.keras.layers import Dense
from tensorflow.keras.models import Sequential
from tensorflow.keras.utils import to_categorical

In [4]:
# pull in training and test data
training_data_path = os.path.join('sentimentsamp.xls')
#test_data_path = os.path.join('sentimentsamp2.xls')

alltrainingdata_df = pd.read_excel(training_data_path)
#alltestdata_df = pd.read_excel(test_data_path)

alltrainingdata_df.head()

id  sentiment                                           sentence ticker  \
0   1          3    All participants will be in a listen-only mode.    CMG   
1   3          3  [Operator Instructions] Please note this event...    CMG   
2   4          3  I would now like to turn the conference over t...    CMG   
3   5          3                                   Please go ahead.    CMG   
4   6          3   Hello, everyone, and welcome to our third qua...    CMG   

                                          call_title       speaker  \
0  Chipotle Mexican Grill, Inc. (NYSE:CMG) Q3 201...      Operator   
1  Chipotle Mexican Grill, Inc. (NYSE:CMG) Q3 201...      Operator   
2  Chipotle Mexican Grill, Inc. (NYSE:CMG) Q3 201...      Operator   
3  Chipotle Mexican Grill, Inc. (NYSE:CMG) Q3 201...      Operator   
4  Chipotle Mexican Grill, Inc. (NYSE:CMG) Q3 201...  Ashish Kohli   

           call_section  
0  operator_instruction  
1  operator_instruction  
2  operator_instruction  
3  operator_instruction  
4          presentation

In [5]:
# extract label data
y_train_df = pd.DataFrame(alltrainingdata_df['sentiment'])
#y_test_df = pd.DataFrame(alltestdata_df['sentiment'])

y_train_categorical = to_categorical(y_train_df)
#y_test_categorical = to_categorical(y_test_df)

y_train_categorical[:10]

array([[0., 0., 0., 1., 0., 0.],
       [0., 0., 0., 1., 0., 0.],
       [0., 0., 0., 1., 0., 0.],
       [0., 0., 0., 1., 0., 0.],
       [0., 0., 0., 1., 0., 0.],
       [0., 0., 0., 1., 0., 0.],
       [0., 0., 0., 1., 0., 0.],
       [0., 0., 0., 1., 0., 0.],
       [0., 0., 0., 1., 0., 0.],
       [0., 0., 0., 1., 0., 0.]], dtype=float32)

In [6]:
# extract input data
X_train_df = pd.DataFrame(alltrainingdata_df['sentence'])
#X_test_df = pd.DataFrame(alltestdata_df['sentence'])

X_train_df.head()

sentence
0    All participants will be in a listen-only mode.
1  [Operator Instructions] Please note this event...
2  I would now like to turn the conference over t...
3                                   Please go ahead.
4   Hello, everyone, and welcome to our third qua...

In [32]:
from sklearn.feature_extraction.text import TfidfVectorizer

In [33]:
tfidf_vectorizer = TfidfVectorizer(use_idf=True)
toylist = ['All participants will be in a listen-only mode.', 'Please go ahead and go.', 'Hello, all, and welcome.', '[Operator Instructions] Please note this event.']
tfidf_vectorizer_vectors = tfidf_vectorizer.fit_transform(toylist)

In [42]:
#first_vector_tfidfvectorizer = tfidf_vectorizer_vectors[0]
print(tfidf_vectorizer_vectors)

  (0, 1)	0.2855815033388837
  (0, 14)	0.36222392540501064
  (0, 18)	0.36222392540501064
  (0, 3)	0.36222392540501064
  (0, 7)	0.36222392540501064
  (0, 9)	0.36222392540501064
  (0, 12)	0.36222392540501064
  (0, 10)	0.36222392540501064
  (1, 15)	0.3155366632994909
  (1, 5)	0.8004364950338771
  (1, 0)	0.4002182475169386
  (1, 2)	0.3155366632994909
  (2, 1)	0.43779123108611473
  (2, 2)	0.43779123108611473
  (2, 6)	0.5552826649411127
  (2, 17)	0.5552826649411127
  (3, 15)	0.3325241986862672
  (3, 13)	0.4217647821447532
  (3, 8)	0.4217647821447532
  (3, 11)	0.4217647821447532
  (3, 16)	0.4217647821447532
  (3, 4)	0.4217647821447532


In [1]:
df = pd.DataFrame(first_vector_tfidfvectorizer.T.todense(), index=tfidf_vectorizer.get_feature_names(), columns=["tfidf"])
df

NameError: name 'pd' is not defined

In [30]:
count_vector = cv.transform(toylist)
tf_idf_vector = tfidf_transformer.transform(count_vector)

In [31]:
feature_names = cv.get_feature_names()
first_document_vector = tf_idf_vector[0]
df = pd.DataFrame(first_document_vector.T.todense(), index=feature_names, columns=["tfidf"])
df.sort_values(by=["tfidf"], ascending=False)

tfidf
listen        0.362224
in            0.362224
participants  0.362224
only          0.362224
mode          0.362224
will          0.362224
be            0.362224
all           0.285582
hello         0.000000
go            0.000000
instructions  0.000000
event         0.000000
note          0.000000
operator      0.000000
and           0.000000
please        0.000000
this          0.000000
welcome       0.000000
ahead         0.000000

In [7]:
# begin calculation to score/weigh sentences
# build necessary lists and dictionaries
train_word_set = ""
train_sentence_list = []
train_dict_list = []
for row in range(len(X_train_df)):
    cleartoken = X_train_df.loc[row, "sentence"].lower().split()
    train_sentence_list.append(cleartoken)
    train_dict_list.append(set(cleartoken))
    train_word_set = set(train_word_set).union(set(cleartoken))
    
# test_word_set = ""
# test_sentence_list = []
# test_dict_list = []
# for row in range(len(X_test_df)):
#     cleartoken = X_test_df.loc[row, "sentence"].lower().split()
#     test_sentence_list.append(cleartoken)
#     test_dict_list.append(set(cleartoken))
#     test_word_set = set(test_word_set).union(set(cleartoken))

for i in range(len(train_dict_list)):
    train_dict_list[i] = dict.fromkeys(train_dict_list[i], 0)
# for i in range(len(test_dict_list)):
#     test_dict_list[i] = dict.fromkeys(test_dict_list[i], 0)

train_word_dict = dict.fromkeys(train_word_set, 0)
#test_word_dict = dict.fromkeys(test_word_set, 0)

print(train_dict_list)

[{'in': 0, 'listen-only': 0, 'all': 0, 'be': 0, 'a': 0, 'will': 0, 'mode.': 0, 'participants': 0}, {'note': 0, 'recorded.': 0, 'being': 0, '[operator': 0, 'this': 0, 'event': 0, 'please': 0, 'is': 0, 'instructions]': 0}, {'turn': 0, 'over': 0, 'global': 0, 'would': 0, 'now': 0, 'to': 0, 'head': 0, 'conference': 0, 'of': 0, 'like': 0, 'kohli,': 0, 'ir.': 0, 'i': 0, 'the': 0, 'ashish': 0}, {'go': 0, 'please': 0, 'ahead.': 0}, {'quarter': 0, 'to': 0, 'hello,': 0, '2019': 0, 'welcome': 0, 'our': 0, 'call.': 0, 'earnings': 0, 'and': 0, 'everyone,': 0, 'third': 0}, {'access': 0, 'now,': 0, 'should': 0, 'you': 0, 'have': 0, 'by': 0, 'to': 0, 'our': 0, 'press': 0, 'release.': 0, 'earnings': 0}, {'openings,': 0, 'you': 0, 'effective': 0, 'by': 0, 'future': 0, 'begin': 0, 'g&a': 0, 'forward-looking': 0, 'expenses.': 0, 'and': 0, 'rate': 0, 'in': 0, 'about': 0, 'comparable': 0, 'constitute': 0, 'financial': 0, 'i': 0, 'presentation': 0, 'certain': 0, 'business': 0, 'will': 0, 'reminding': 0, 'inc

In [8]:
# add word counts to dictionaries
for i in range(len(train_sentence_list)):
    for word in train_sentence_list[i]:
        train_dict_list[i][word] += 1

# for i in range(len(test_sentence_list)):
#     for word in test_sentence_list[i]:
#         test_dict_list[i][word] += 1
        
print(train_dict_list)

[{'in': 1, 'listen-only': 1, 'all': 1, 'be': 1, 'a': 1, 'will': 1, 'mode.': 1, 'participants': 1}, {'note': 1, 'recorded.': 1, 'being': 1, '[operator': 1, 'this': 1, 'event': 1, 'please': 1, 'is': 1, 'instructions]': 1}, {'turn': 1, 'over': 1, 'global': 1, 'would': 1, 'now': 1, 'to': 2, 'head': 1, 'conference': 1, 'of': 1, 'like': 1, 'kohli,': 1, 'ir.': 1, 'i': 1, 'the': 1, 'ashish': 1}, {'go': 1, 'please': 1, 'ahead.': 1}, {'quarter': 1, 'to': 1, 'hello,': 1, '2019': 1, 'welcome': 1, 'our': 1, 'call.': 1, 'earnings': 1, 'and': 1, 'everyone,': 1, 'third': 1}, {'access': 1, 'now,': 1, 'should': 1, 'you': 1, 'have': 1, 'by': 1, 'to': 1, 'our': 1, 'press': 1, 'release.': 1, 'earnings': 1}, {'openings,': 1, 'you': 1, 'effective': 1, 'by': 1, 'future': 1, 'begin': 1, 'g&a': 1, 'forward-looking': 1, 'expenses.': 1, 'and': 3, 'rate': 1, 'in': 1, 'about': 2, 'comparable': 1, 'constitute': 1, 'financial': 1, 'i': 1, 'presentation': 1, 'certain': 1, 'business': 1, 'will': 1, 'reminding': 1, 'inc

In [9]:
# fill tf lists
train_tf_list = []
#test_tf_list = []
def compute_tf(wd, l):
    tf = {}
    sum_nk = len(l)
    for word, count in wd.items():
        tf[word] = count/sum_nk
    return tf

for i in range(len(train_dict_list)):
    train_tf_list.append(compute_tf(train_dict_list[i], train_sentence_list[i]))  
# for i in range(len(test_dict_list)):
#     test_tf_list.append(compute_tf(test_dict_list[i], test_sentence_list[i]))

print(train_tf_list)

[{'in': 0.125, 'listen-only': 0.125, 'all': 0.125, 'be': 0.125, 'a': 0.125, 'will': 0.125, 'mode.': 0.125, 'participants': 0.125}, {'note': 0.1111111111111111, 'recorded.': 0.1111111111111111, 'being': 0.1111111111111111, '[operator': 0.1111111111111111, 'this': 0.1111111111111111, 'event': 0.1111111111111111, 'please': 0.1111111111111111, 'is': 0.1111111111111111, 'instructions]': 0.1111111111111111}, {'turn': 0.0625, 'over': 0.0625, 'global': 0.0625, 'would': 0.0625, 'now': 0.0625, 'to': 0.125, 'head': 0.0625, 'conference': 0.0625, 'of': 0.0625, 'like': 0.0625, 'kohli,': 0.0625, 'ir.': 0.0625, 'i': 0.0625, 'the': 0.0625, 'ashish': 0.0625}, {'go': 0.3333333333333333, 'please': 0.3333333333333333, 'ahead.': 0.3333333333333333}, {'quarter': 0.09090909090909091, 'to': 0.09090909090909091, 'hello,': 0.09090909090909091, '2019': 0.09090909090909091, 'welcome': 0.09090909090909091, 'our': 0.09090909090909091, 'call.': 0.09090909090909091, 'earnings': 0.09090909090909091, 'and': 0.0909090909

In [10]:
# fill idf lists
train_idf = dict.fromkeys(train_word_dict.keys(), 0)
#test_idf = dict.fromkeys(test_word_dict.keys(), 0)

def compute_idf(strings_list, idf):
    n = len(strings_list)

    for l in strings_list:
        for word, count in l.items():
            if count > 0:
                idf[word] += 1
    for word, v in idf.items():
        idf[word] = math.log(n/float(v))
    return idf

train_idf = compute_idf(train_dict_list, train_idf)
#test_idf = compute_idf(test_dict_list, test_idf)

print(train_idf)

{'done': 4.54063166485052, 'plant': 7.313220387090301, 'i’': 8.006367567650246, 'takes.': 8.006367567650246, 'given': 4.915325114291931, 'touching': 8.006367567650246, 'instance': 8.006367567650246, 'gamers': 6.907755278982137, 'maintenance.': 8.006367567650246, "development's": 7.313220387090301, 'offset': 4.451019506160833, 'does': 5.0106352940962555, 'occasion.': 8.006367567650246, '$139': 8.006367567650246, 'kind': 3.912023005428146, 'lives': 7.313220387090301, 'living': 8.006367567650246, 'embrace': 8.006367567650246, 'airframer': 8.006367567650246, 'job': 5.703782474656201, 'preferred': 7.313220387090301, 'charges': 7.313220387090301, 'that,': 4.0943445622221, 'agreement': 5.703782474656201, 'cab,': 8.006367567650246, 'positioned': 6.907755278982137, 'incrementally': 8.006367567650246, 'center': 5.44141821018871, 'topics.': 8.006367567650246, 'requirement': 8.006367567650246, 'labor.': 8.006367567650246, 'shareholder': 6.396929655216146, 'clearly,': 6.620073206530356, '47': 8.006

In [11]:
# calculate tf-idf lists
train_tf_idf_list = []
#test_tf_idf_list = []
def compute_tf_idf(tf, idf):
    tf_idf = dict.fromkeys(tf.keys(), 0)
    for word, v in tf.items():
        tf_idf[word] = v * idf[word]
    return tf_idf

for i in range(len(train_tf_list)):
    train_tf_idf_list.append(compute_tf_idf(train_tf_list[i], train_idf))
# for i in range(len(test_tf_list)):
#     test_tf_idf_list.append(compute_tf_idf(test_tf_list[i], test_idf))

print(train_tf_idf_list)

[{'in': 0.15091396319893133, 'listen-only': 0.8275091508162945, 'all': 0.3913962805561369, 'be': 0.29077436982914745, 'a': 0.17564218111517133, 'will': 0.3551976992158416, 'mode.': 0.8634694098727671, 'participants': 0.8275091508162945}, {'note': 0.6454603322571142, 'recorded.': 0.7675283643313485, 'being': 0.4769772778828821, '[operator': 0.6231635883168751, 'this': 0.23808182133912772, 'event': 0.7355636896144839, 'please': 0.4825339912800667, 'is': 0.19094544527649582, 'instructions]': 0.6454603322571142}, {'turn': 0.28000044018963033, 'over': 0.20438556995348445, 'global': 0.2837894790531575, 'would': 0.2249780200241246, 'now': 0.19763628007447848, 'to': 0.11453634148426939, 'head': 0.38841300615138696, 'conference': 0.2899419836039858, 'of': 0.06236639909799791, 'like': 0.20329858603399265, 'kohli,': 0.5003979729781404, 'ir.': 0.5003979729781404, 'i': 0.12170277325427811, 'the': 0.043238420957885416, 'ashish': 0.5003979729781404}, {'go': 1.277326765918203, 'please': 1.447601973840

In [12]:
# add together weight of words for each sentence, add to dataframe
# for row in range(len(X_train_df)):
#     sentence_weight = []
#     for word in train_tf_idf_list[row]:
#         sentence_weight.append(train_tf_idf_list[row][word])
#     X_train_df.loc[row, "sentence_weight"] = sentence_weight

# for row in range(len(X_test_df)):
#     sentence_weight = 0
#     for word in test_tf_idf_list[row]:
#         sentence_weight.append(test_tf_idf_list[row][word])
#     X_test_df.loc[row, "sentence_weight"] = sentence_weight
train_sentence_weight = []
for row in range(len(X_train_df)):
    sent = []
    for word in train_tf_idf_list[row]:
        sent.append(train_tf_idf_list[row][word])
    train_sentence_weight.append(sent)
#for row in range(len(train_sentence_weight)):
    #X_test_df.loc[row, "sentence_weight"] = train_sentence_weight[row]
weight_series = pd.Series(train_sentence_weight)
X_train_df["sentence_weight"] = weight_series
    
X_train_df.head()

sentence  \
0    All participants will be in a listen-only mode.   
1  [Operator Instructions] Please note this event...   
2  I would now like to turn the conference over t...   
3                                   Please go ahead.   
4   Hello, everyone, and welcome to our third qua...   

                                     sentence_weight  
0  [0.15091396319893133, 0.8275091508162945, 0.39...  
1  [0.6454603322571142, 0.7675283643313485, 0.476...  
2  [0.28000044018963033, 0.20438556995348445, 0.2...  
3  [1.277326765918203, 1.4476019738402002, 1.6236...  
4  [0.2792630576835959, 0.08329915744310501, 0.72...

In [13]:
from sklearn.model_selection import train_test_split

X_train, X_test, y_train, y_test = train_test_split(X_train_df['sentence_weight'], y_train_categorical, test_size=0.25,random_state=109)

In [21]:
# shape input data
#X_train_df = pd.DataFrame(X_train_df["sentence_weight"])
#X_test_df = pd.DataFrame(X_test_df["sentence_weight"])

#X_train = X_train_df.values
#X_test = X_test_df.values

#X_train = X_train.reshape(-1, 1)
X_train.shape
y_train.shape

(2250, 6)

In [17]:
# scale input data
X_scaler = StandardScaler().fit(X_train)

X_train_scaled = X_scaler.transform(X_train)
#X_test_scaled = X_scaler.transform(X_test)

ValueError: setting an array element with a sequence.

In [16]:
# build model
model = Sequential()
number_inputs = 1
number_hidden_nodes = 12
model.add(Dense(units=number_hidden_nodes, activation='relu', input_dim=number_inputs))

number_classes = 6
model.add(Dense(units=number_classes, activation='softmax'))

model.summary()

Model: "sequential"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
dense (Dense)                (None, 12)                24        
_________________________________________________________________
dense_1 (Dense)              (None, 6)                 78        
Total params: 102
Trainable params: 102
Non-trainable params: 0
_________________________________________________________________


In [22]:
model.compile(optimizer='adam', loss='categorical_crossentropy', metrics=['accuracy'])

model.fit(X_train, y_train, epochs=500, shuffle=True, verbose=2)

Train on 2250 samples
Epoch 1/500


ValueError: setting an array element with a sequence.

In [16]:
model_loss, model_accuracy = model.evaluate(X_test_scaled, y_test_categorical, verbose=0)
print(f"Loss: {model_loss}, Accuracy: {model_accuracy}")

Loss: 0.9791341071128845, Accuracy: 0.6570000052452087


In [3]:
import findspark
findspark.init()
import pyspark

ValueError: Couldn't find Spark, make sure SPARK_HOME env is set or Spark is in an expected location (e.g. from homebrew installation).

In [2]:
dataframe = spark.createDataFrame([
    (0, "Spark is great"),
    (1, "We are learning Spark"),
    (2, "Spark is better than hadoop no doubt")
], ["id", "sentence"])

NameError: name 'spark' is not defined